# Assignment 6

## Datasets

In [1]:
import pandas as pd

lineitem = pd.read_csv('20241216_export_pharmacy_receiptdata_lineitem.csv')
print(f"Length of lineitem: {len(lineitem)}")
lineitem.head()

/var/folders/cw/_c2hk43d7v31tkx47_ccfpwr0000gn/T/ipykernel_12095/2419095611.py:3: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  lineitem = pd.read_csv('20241216_export_pharmacy_receiptdata_lineitem.csv')


Length of lineitem: 12150015


transaction_id       pzn  amount  quantity
0  4d327c97-99b3-4800-ba76-000000020967  12557966     893         1
1  4d327ded-0172-4f49-8489-000000001966   9298432    2200         1
2  4d327ded-0172-4f49-8489-000000001966   9605236    1180         1
3  4d328cea-54ad-4ba2-b851-000000012421   1126111     179         1
4  4d328cea-54ad-4ba2-b851-000000012421   2013219     299         1

In [2]:
receipt = pd.read_csv('20241216_export_pharmacy_receiptdata_receipt.csv')
print(f"Length {len(receipt)}")
receipt.head()

Length 6571356


transaction_id  retailer_id      gln  zipcode_area  \
0  0cd27cab-fa36-410e-8a05-000000898986         1051  1036331            82   
1  01e18514-bc0b-4f47-b26e-000000898836         1051  1036331            82   
2  90481553-50e3-4b89-b916-000000899679         1051  1036331            82   
3  d506586f-890b-45e3-83b4-000000899870         1051  1036331            82   
4  9d8ff431-c018-48e2-a6d1-000000900137         1051  1036331            82   

   pos_id            timestamp  
0       1  2024-11-07 13:51:22  
1       1  2024-11-07 14:28:04  
2       1  2024-11-07 14:45:09  
3       1  2024-11-07 15:11:00  
4       1  2024-11-07 15:36:42

In [3]:
products = pd.read_csv('20241216_export_pharmacy_receiptdata_product.csv')
print(f"Length {len(products)}")
products.head()

Length 46550


pzn                product_name
0  16762396   HANSAPLAST SPRUEHPFLASTER
1   3643419     NICORETTE 2MG FRESHMINT
2   7263487   PARACETAMOL RATIO LOESUNG
3   9298432        EUCERIN SUN KIDS 50+
4   4778073  HANSAPLAST FIX CLA5MX2.5CM

In [4]:
unique_pzn_count_lineitem = lineitem['pzn'].nunique()
print(f"Number of unique PZNs: {unique_pzn_count_lineitem}")

Number of unique PZNs: 65191


In [5]:
unique_pzn_count = products['pzn'].nunique()
print(f"Number of unique PZNs: {unique_pzn_count}")

Number of unique PZNs: 46550


In [6]:
top_250_pzns = lineitem['pzn'].value_counts().head(250).index.tolist()

top_250_lineitems = lineitem[lineitem['pzn'].isin(top_250_pzns)]

print(f"Number of rows in the filtered dataset: {len(top_250_lineitems)}")
print(f"Number of unique PZNs: {top_250_lineitems['pzn'].nunique()}")
top_250_lineitems.head()

Number of rows in the filtered dataset: 7229033
Number of unique PZNs: 250


transaction_id       pzn  amount  quantity
1  4d327ded-0172-4f49-8489-000000001966   9298432    2200         1
3  4d328cea-54ad-4ba2-b851-000000012421   1126111     179         1
4  4d328cea-54ad-4ba2-b851-000000012421   2013219     299         1
5  4d328cea-54ad-4ba2-b851-000000012421  12550409     749         1
6  4d328f07-8bc4-4b98-9178-000000070091   5566226     681         1

In [7]:
merged_data = pd.merge(top_250_lineitems, products, on='pzn', how='inner')

merged_data = merged_data.drop_duplicates(subset='pzn').head(250)
merged_data.to_csv('250_top_pzns.csv')

print(f"Number of rows in the filtered dataset: {len(merged_data)}")
merged_data.head()

Number of rows in the filtered dataset: 250


transaction_id       pzn  amount  quantity  \
0  4d327ded-0172-4f49-8489-000000001966   9298432    2200         1   
1  4d328cea-54ad-4ba2-b851-000000012421   1126111     179         1   
2  4d328cea-54ad-4ba2-b851-000000012421   2013219     299         1   
3  4d328cea-54ad-4ba2-b851-000000012421  12550409     749         1   
4  4d328f07-8bc4-4b98-9178-000000070091   5566226     681         1   

              product_name  
0     EUCERIN SUN KIDS 50+  
1  PARACETAMOL RATIO 500MG  
2   IBU 400 AKUT 1A PHARMA  
3             FENISTIL GEL  
4      BRONCHIPRET SAFT TE

## Apotheke.de
 
https://www.apotheke.de/

In [22]:
import undetected_chromedriver as uc
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import re
import time
import random
import pandas as pd

driver = uc.Chrome(version_main=131)


def random_delay(min_time=3, max_time=7):
    time.sleep(random.uniform(min_time, max_time))

def close_consent_banner():
    try:
        WebDriverWait(driver, 5).until(
            EC.presence_of_element_located((By.CLASS_NAME, "consent_footer"))
        )
        
        accept_button = driver.find_element(By.XPATH, "//button[contains(text(), 'Einverstanden')]")
        accept_button.click()
        print("Consent banner closed.")
        random_delay()
    except Exception as e:
        print("No consent banner found or already closed.")

def search_pzn_and_extract(pzn, product_name):
    try:
        driver.get(f"https://www.apotheke.de/search.php?query={pzn}")
        random_delay()

        close_consent_banner()

        characteristics = []
        try:
            characteristics_container = driver.find_element(By.XPATH, "//div[@class='d-none d-md-block']/div[@class='text-highlight']/ul")
            characteristics_items = characteristics_container.find_elements(By.TAG_NAME, "li")
            for item in characteristics_items:
                characteristics.append(item.text.strip())
        except Exception as e:
            print(f"Fehler beim Extrahieren der Produkteigenschaften: {e}")

        product_link = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.XPATH, "//div[@class='col-4 col-md-3']/a"))
        )
        product_link.click()
        random_delay()

        WebDriverWait(driver, 10).until(
            EC.presence_of_element_located((By.CLASS_NAME, "product_detail_price"))
        )

        price_element = driver.find_element(By.CLASS_NAME, "product_detail_price")
        price = price_element.text.replace("\n", "").strip()

        package_size_element = driver.find_element(By.XPATH, "//div[@class='edd-value' and @data-ref='value']")
        package_size = package_size_element.text.strip()

        product_info_element = driver.find_element(By.CLASS_NAME, "product_info_information_area_right")
        product_info = product_info_element.text.strip()

        clean_product_info = re.sub(r'\xAD', '', product_info)

        # Splitte den bereinigten Text in Zeilen
        lines = clean_product_info.split('\n')

        # Initialisiere die Variablen
        manufacturer = "Unbekannt"
        brand = "Unbekannt"
        type_ = "Unbekannt"

        # Durchsuche jede Zeile nach dem passenden Schlüsselwort
        for line in lines:
            print(f"Debug: Verarbeite Zeile: {repr(line)}")  # Debug-Ausgabe
            if "Hersteller:" in line:
                manufacturer = line.split("Hersteller:")[1].strip()
            elif "Marke:" in line:
                brand = line.split("Marke:")[1].strip()
            elif "Darreichung:" in line:
                type_ = line.split("Darreichung:")[1].strip()


        print(f"Successfully extracted data for PZN {pzn}")
        print(f"Price: {price}, Package Size: {package_size}, Manufacturer: {manufacturer}, Brand: {brand}, Type: {type_}, Characteristics {characteristics}")

        return {
            "pzn": pzn,
            "product_name": product_name,
            "price": price,
            "package_size": package_size,
            "manufacturer": manufacturer,
            "brand": brand,
            "type": type_,
            "characteristics": characteristics,
        }

    except Exception as e:
        print(f"Error extracting data for PZN {pzn}: {e}")
        driver.save_screenshot(f"error_{pzn}.png")
        return None

merged_data = pd.read_csv('250_top_pzns.csv')
pzn_product_pairs = merged_data[['pzn', 'product_name']].values.tolist()

results = []
for pzn, product_name in pzn_product_pairs:
    product_info = search_pzn_and_extract(str(pzn), product_name)
    if product_info:
        print(product_info)
        results.append(product_info)

if results:
    df = pd.DataFrame(results)
    df.to_csv("apotheke_products.csv", index=False)
    print("Data successfully saved to apotheke_products.csv")
else:
    print("No data extracted. CSV file not created.")

driver.quit()

Consent banner closed.
Debug: Verarbeite Zeile: 'PZN: 09298432'
Debug: Verarbeite Zeile: 'Hersteller: Beiersdorf AG Eucerin'
Debug: Verarbeite Zeile: 'Marke: Eucerin'
Debug: Verarbeite Zeile: 'Grundpreis: 96,45€/1 l'
Debug: Verarbeite Zeile: 'Darreichung: Spray'
Successfully extracted data for PZN 9298432
Price: 19,29*, Package Size: 200 ml, Manufacturer: Beiersdorf AG Eucerin, Brand: Eucerin, Type: Spray, Characteristics ['Sehr hoher Sonnenschutz für Kinder', 'Schutz vor UVA/UVB-Strahlung und HEV-Licht', 'Extra wasserfest und unparfümiert', 'Beruhigt und schützt empfindliche Haut, Hautverträglichkeit dermatologisch bestätigt', 'Auch bei Neurodermitis anwendbar']
{'pzn': '9298432', 'product_name': 'EUCERIN SUN KIDS 50+', 'price': '19,29*', 'package_size': '200 ml', 'manufacturer': 'Beiersdorf AG Eucerin', 'brand': 'Eucerin', 'type': 'Spray', 'characteristics': ['Sehr hoher Sonnenschutz für Kinder', 'Schutz vor UVA/UVB-Strahlung und HEV-Licht', 'Extra wasserfest und unparfümiert', 'Beru

## Categorization

In [10]:
import pandas as pd

apotheke_products = pd.read_csv('apotheke_products.csv')

print(f"Number of rows in the apotheke_products: {len(apotheke_products)}")
print(apotheke_products.head())

Number of rows in the apotheke_products: 247
        pzn             product_name   price package_size  \
0   9298432     EUCERIN SUN KIDS 50+  19,29*       200 ml   
1   1126111  PARACETAMOL RATIO 500MG   3,79*       20 stk   
2   2013219   IBU 400 AKUT 1A PHARMA   3,49*       20 stk   
3  12550409             FENISTIL GEL   9,39*         30 g   
4   5566226      BRONCHIPRET SAFT TE   6,39*        50 ml   

            manufacturer                   brand           type  \
0  Beiersdorf AG Eucerin                 Eucerin          Spray   
1        ratiopharm GmbH  Paracetamol-ratiopharm      Tabletten   
2        1 A Pharma GmbH  Ibu-400 akut 1A Pharma  Filmtabletten   
3    Haleon Germany GmbH                Fenistil            Gel   
4           Bionorica SE             Bronchipret           Saft   

                                     characteristics  
0  ['Sehr hoher Sonnenschutz für Kinder', 'Schutz...  
1  ['Zur Behandlung von Schmerzen und Fieber', 'G...  
2  ['Der Klassiker b

### by Characteristic

In [12]:
import ast

# Function to extract characteristics from the row
def extract_characteristics(row):
    try:
        return ast.literal_eval(row['characteristics'])
    except Exception as e:
        print(f"Error with PZN {row['pzn']}: {str(e)}")
        return []

# Apply the function to extract characteristics
apotheke_products['extracted_characteristics'] = apotheke_products.apply(extract_characteristics, axis=1)

characteristics_list = []

# Fill the list with the characteristics and the associated PZN
for index, row in apotheke_products.iterrows():
    for characteristic in row['extracted_characteristics']:
        characteristics_list.append({'pzn': row['pzn'], 'characteristic': characteristic})

# Create a new DataFrame from the list
characteristics_df = pd.DataFrame(characteristics_list)

# Count the occurrences of each characteristic and aggregate the PZNs
result = characteristics_df.groupby('characteristic').agg(
    pzn_array=('pzn', lambda x: list(x)),
    count=('pzn', 'size')
).reset_index()

print(f"Number of Characteristic {len(result)}")

# Sort by the count of PZNs in descending order
result = result.sort_values(by='count', ascending=False)
result.head()

Number of Characteristic 844


characteristic  \
240              Für Erwachsene und Kinder ab 6 Jahren   
314                                    Gut verträglich   
154  Dexpanthenol unterstützt die Heilung der gerei...   
55        Befreit und pflegt die Nase mit dem WirkPlus   
403                                          Latexfrei   

                                             pzn_array  count  
240  [999831, 4300124, 2663704, 2218855, 2158142, 9...      8  
314  [2013219, 3045316, 202465, 2158142, 4100218, 4...      8  
154  [705309, 15863497, 2882760, 2882777, 10065578,...      6  
55   [705309, 15863497, 2882760, 2882777, 10065578,...      6  
403  [16739724, 16759247, 16760115, 16760138, 16760...      6

### by Type

In [15]:
categories_by_type = apotheke_products.groupby('type')['pzn'].apply(list).reset_index()

categories_by_type['count'] = categories_by_type['pzn'].apply(len)

print(f"Number of rows in the types: {len(categories_by_type)}")
categories_by_type = categories_by_type.sort_values(by='count', ascending=False)
categories_by_type.head()

Number of rows in the types: 51


type                                                pzn  count
5             Creme  [18201503, 10832664, 16154610, 16015570, 19878...     41
9     Filmtabletten  [2013219, 1830169, 2662780, 1830152, 1094724, ...     22
32         Pflaster  [16742761, 16739724, 16760144, 16759247, 47780...     20
29       Nasenspray  [999831, 999854, 12521566, 705309, 15863497, 1...     16
24  Lutschtabletten  [826616, 1712470, 7727923, 12700079, 6866410, ...     12

### by Manufacturer

In [14]:
categories_by_manufacturer = apotheke_products.groupby('manufacturer')['pzn'].apply(list).reset_index()

categories_by_manufacturer['count'] = categories_by_manufacturer['pzn'].apply(len)

print(f"Number of rows in the manufacturers: {len(categories_by_manufacturer)}")
categories_by_manufacturer = categories_by_manufacturer.sort_values(by='count', ascending=False)
categories_by_manufacturer.head()

Number of rows in the manufacturers: 40


manufacturer  \
7          Beiersdorf AG Eucerin   
6                  Beiersdorf AG   
18  Johnson & Johnson GmbH (OTC)   
21   MCM KLOSTERFRAU Vertr. GmbH   
5               Bayer Vital GmbH   

                                                  pzn  count  
7   [9298432, 7415483, 9508059, 18201503, 8796286,...     56  
6   [16742761, 16739724, 16760144, 16759247, 17313...     21  
18  [2340421, 1094724, 676714, 1689854, 4300124, 2...     18  
21  [744255, 705309, 826616, 15863497, 15203513, 1...     16  
5   [1578847, 3227112, 4002065, 1987824, 1580241, ...     15

In [15]:
categories_by_manufacturer[['manufacturer']].to_csv("manufacturers_names.csv", index=False)

print("Manufacturers' names have been successfully saved as 'manufacturers_names.csv'.")

Manufacturers' names have been successfully saved as 'manufacturers_names.csv'.


### by Brand

In [17]:
categories_by_brand = apotheke_products.groupby('brand')['pzn'].apply(list).reset_index()

categories_by_brand['count'] = categories_by_brand['pzn'].apply(len)

print(f"Number of rows in the brands: {len(categories_by_brand)}")
categories_by_brand = categories_by_brand.sort_values(by='count', ascending=False)
categories_by_brand.head()

Number of rows in the brands: 96


brand                                                pzn  count
24     Eucerin  [9298432, 7415483, 9508059, 18201503, 8796286,...     56
31  Hansaplast  [16742761, 16739724, 16760144, 16759247, 17313...     21
65      Olynth  [2340421, 4300124, 1014470, 5507353, 2186397, ...      7
94       nasic  [705309, 15863497, 2882760, 2882777, 10065578,...      6
10   Bepanthen  [1578847, 1987824, 1580241, 1578818, 1578681, ...      6

### by Combined category (manufacturer + type)

In [18]:
apotheke_products['combined_category'] = apotheke_products['manufacturer'] + " - " + apotheke_products['type']

categories_combined = apotheke_products.groupby('combined_category')['pzn'].apply(list).reset_index()

categories_combined['count'] = categories_combined['pzn'].apply(len)

print(f"Number of rows in the combined categories: {len(categories_combined)}")
categories_combined = categories_combined.sort_values(by='count', ascending=False)
categories_combined.head()

Number of rows in the combined categories: 123


combined_category  \
24             Beiersdorf AG Eucerin - Creme   
19                  Beiersdorf AG - Pflaster   
78  MCM KLOSTERFRAU Vertr. GmbH - Nasenspray   
30            Beiersdorf AG Eucerin - Lotion   
58                  Hexal AG - Filmtabletten   

                                                  pzn  count  
24  [18201503, 10832664, 16154610, 16015570, 17553...     30  
19  [16742761, 16739724, 16760144, 16759247, 47780...     19  
78  [705309, 15863497, 2882760, 2882777, 10065578,...      6  
30  [8454700, 11678082, 11678142, 3815725, 1167800...      6  
58      [1830169, 1830152, 13917740, 68972, 14171188]      5

### by Combined category (manufacturer + brand)

In [19]:
apotheke_products['combined_category_man_brand'] = apotheke_products['manufacturer'] + " - " + apotheke_products['brand']

categories_man_brand = apotheke_products.groupby('combined_category_man_brand')['pzn'].apply(list).reset_index()

categories_man_brand['count'] = categories_man_brand['pzn'].apply(len)

print(f"Number of rows in the combined categories: {len(categories_man_brand)}")
categories_man_brand = categories_man_brand.sort_values(by='count', ascending=False)
categories_man_brand.head()

Number of rows in the combined categories: 100


combined_category_man_brand  \
18        Beiersdorf AG Eucerin - Eucerin   
17             Beiersdorf AG - Hansaplast   
49  Johnson & Johnson GmbH (OTC) - Olynth   
59    MCM KLOSTERFRAU Vertr. GmbH - nasic   
12           Bayer Vital GmbH - Bepanthen   

                                                  pzn  count  
18  [9298432, 7415483, 9508059, 18201503, 8796286,...     56  
17  [16742761, 16739724, 16760144, 16759247, 17313...     21  
49  [2340421, 4300124, 1014470, 5507353, 2186397, ...      7  
59  [705309, 15863497, 2882760, 2882777, 10065578,...      6  
12  [1578847, 1987824, 1580241, 1578818, 1578681, ...      6

### by Combined category (type + brand)

In [20]:
apotheke_products['combined_category_type_brand'] = apotheke_products['type'] + " - " + apotheke_products['brand']

categories_type_brand = apotheke_products.groupby('combined_category_type_brand')['pzn'].apply(list).reset_index()

categories_type_brand['count'] = categories_type_brand['pzn'].apply(len)

print(f"Number of rows in the combined categories: {len(categories_type_brand)}")
categories_type_brand = categories_type_brand.sort_values(by='count', ascending=False)
categories_type_brand.head()

Number of rows in the combined categories: 138


combined_category_type_brand  \
16              Creme - Eucerin   
97        Pflaster - Hansaplast   
74             Lotion - Eucerin   
92           Nasenspray - nasic   
81  Lutschtabletten - Neo-Angin   

                                                  pzn  count  
16  [18201503, 10832664, 16154610, 16015570, 17553...     30  
97  [16742761, 16739724, 16760144, 16759247, 47780...     19  
74  [8454700, 11678082, 11678142, 3815725, 1167800...      6  
92  [705309, 15863497, 2882760, 2882777, 10065578,...      6  
81                [826616, 11160178, 826562, 8997145]      4

### by Price range

In [21]:
apotheke_products['price_euro'] = apotheke_products['price'].str.replace(',', '.').str.extract(r'(\d+\.\d+)').astype(float)

bins = [0, 5, 10, 20, 50, 100]
labels = ['0-5€', '5-10€', '10-20€', '20-50€', '50-100€']

apotheke_products['price_range'] = pd.cut(apotheke_products['price_euro'], bins=bins, labels=labels)

categories_by_price = apotheke_products.groupby('price_range')['pzn'].apply(list).reset_index()

categories_by_price['count'] = categories_by_price['pzn'].apply(len)

categories_by_price.head()

/var/folders/cw/_c2hk43d7v31tkx47_ccfpwr0000gn/T/ipykernel_1675/4249501278.py:8: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  categories_by_price = apotheke_products.groupby('price_range')['pzn'].apply(list).reset_index()


price_range                                                pzn  count
0        0-5€  [1126111, 2013219, 999831, 16742761, 3929274, ...     43
1       5-10€  [12550409, 5566226, 8796286, 1987824, 1580241,...     81
2      10-20€  [9298432, 1578847, 11024417, 744255, 7415483, ...     81
3      20-50€  [9285547, 15257408, 4002065, 16154610, 1601557...     40
4     50-100€                               [18052351, 14171188]      2

### by Unit

In [23]:
apotheke_products['package_unit'] = apotheke_products['package_size'].str.extract(r'([a-zA-Z]+)$')

categories_by_package_unit = apotheke_products.groupby('package_unit')['pzn'].apply(list).reset_index()
categories_by_package_unit['count'] = categories_by_package_unit['pzn'].apply(len)

print(f"Number of rows in the unites: {len(categories_by_package_unit)}")

categories_by_package_unit = categories_by_package_unit.sort_values(by='count', ascending=False)

categories_by_package_unit.head(5)

Number of rows in the unites: 4


package_unit                                                pzn  count
2           ml  [9298432, 5566226, 999831, 11024417, 7415483, ...    124
3          stk  [1126111, 2013219, 744255, 571748, 16742761, 1...     93
1            g  [12550409, 1578847, 1987824, 1580241, 1578818,...     28
0          Pck                                 [18052351, 676789]      2

### Price Ranges for Manufacturer, Brand and Type

In [12]:
bins = [0, 5, 20, 50, 100]
labels = ['Cheap', 'Mid-Range', 'Expensive', 'Super-Expensive']

### by Manufacturer and Price

In [13]:
apotheke_products['price_euro'] = apotheke_products['price'].str.replace(',', '.').str.extract(r'(\d+\.\d+)').astype(float)

avg_price_by_manufacturer = apotheke_products.groupby('manufacturer')['price_euro'].mean().reset_index()

avg_price_by_manufacturer['price_category'] = pd.cut(avg_price_by_manufacturer['price_euro'], bins=bins, labels=labels)

sorted_avg_manufacturer_price = avg_price_by_manufacturer.sort_values(by='price_euro', ascending=True)

sorted_avg_manufacturer_price

manufacturer  price_euro  \
2                                   ALIUD Pharma GmbH    3.140000   
38                        betapharm Arzneimittel GmbH    3.590000   
4                                  Aristo Pharma GmbH    3.690000   
6                                       Beiersdorf AG    4.413810   
0                                     1 A Pharma GmbH    4.490000   
39                                    ratiopharm GmbH    4.826364   
25                                   PAUL HARTMANN AG    5.640000   
11                      Dr. Pfleger Arzneimittel GmbH    6.590000   
37                                Zentiva Pharma GmbH    6.990000   
19                                 Klinge Pharma GmbH    7.290000   
30             STADA Consumer Health Deutschland GmbH    8.412222   
22              MEDICE Arzneimittel Pütter GmbH&Co.KG    8.515000   
12                Engelhard Arzneimittel GmbH & Co.KG    8.590000   
18                       Johnson & Johnson GmbH (OTC)    8.640000   
1                            A. Nattermann & Cie GmbH    9.104286   
23                                    OmniVision GmbH    9.290000   
21                        MCM KLOSTERFRAU Vertr. GmbH    9.383750   
3                    Angelini Pharma Deutschland GmbH    9.490000   
29                                SCHüLKE & MAYR GmbH    9.690000   
15                           HERMES Arzneimittel GmbH   10.140000   
28                 Reckitt Benckiser Deutschland GmbH   10.356667   
26                           Perrigo Deutschland GmbH   10.840000   
35                                 WEBER & WEBER GmbH   10.890000   
9                DR. KADE Pharmazeutische Fabrik GmbH   10.890000   
34                                          Unbekannt   11.356667   
13                      G. Pohl-Boskamp GmbH & Co. KG   11.490000   
27                               ROBUGEN GmbH & Co.KG   11.790000   
5                                    Bayer Vital GmbH   12.323333   
10           Dr. Gerhard Mann Chem.-pharm.Fabrik GmbH   12.590000   
36  WICK Pharma - Zweigniederlassung der Procter &...   12.690000   
16                                Haleon Germany GmbH   13.765000   
14                                   GALENpharma GmbH   13.890000   
8                                        Bionorica SE   14.147143   
31                                   Thea Pharma GmbH   15.190000   
33                        URSAPHARM Arzneimittel GmbH   15.890000   
20                           L'Oreal Deutschland GmbH   16.590000   
17                                           Hexal AG   16.601111   
7                               Beiersdorf AG Eucerin   21.882857   
32                          Trommsdorff GmbH & Co. KG   28.990000   
24            Orthomol pharmazeutische Vertriebs GmbH   57.990000   

     price_category  
2             Cheap  
38            Cheap  
4             Cheap  
6             Cheap  
0             Cheap  
39            Cheap  
25        Mid-Range  
11        Mid-Range  
37        Mid-Range  
19        Mid-Range  
30        Mid-Range  
22        Mid-Range  
12        Mid-Range  
18        Mid-Range  
1         Mid-Range  
23        Mid-Range  
21        Mid-Range  
3         Mid-Range  
29        Mid-Range  
15        Mid-Range  
28        Mid-Range  
26        Mid-Range  
35        Mid-Range  
9         Mid-Range  
34        Mid-Range  
13        Mid-Range  
27        Mid-Range  
5         Mid-Range  
10        Mid-Range  
36        Mid-Range  
16        Mid-Range  
14        Mid-Range  
8         Mid-Range  
31        Mid-Range  
33        Mid-Range  
20        Mid-Range  
17        Mid-Range  
7         Expensive  
32        Expensive  
24  Super-Expensive

In [26]:
import plotly.express as px

category_counts = sorted_avg_manufacturer_price['price_category'].value_counts().reset_index()
category_counts.columns = ['price_category', 'count']

fig = px.pie(
    category_counts,
    values='count',
    names='price_category',
    title='Distribution of Manufacturers by Price Category',
    color_discrete_sequence=px.colors.qualitative.Set3
)

fig.show()

### by Brand and Price

In [36]:
apotheke_products['price_euro'] = apotheke_products['price'].str.replace(',', '.').str.extract(r'(\d+\.\d+)').astype(float)

avg_price_by_brand = apotheke_products.groupby('brand')['price_euro'].mean().reset_index()

avg_price_by_brand['price_category'] = pd.cut(avg_price_by_brand['price_euro'], bins=bins, labels=labels)

sorted_avg_brand_price = avg_price_by_brand.sort_values(by='price_euro', ascending=True)

sorted_avg_brand_price.head()

brand  price_euro   price_category
29     Gingium       65.99  Super-Expensive
66    Orthomol       57.99  Super-Expensive
73     Priorin       44.99        Expensive
83  Tromcardin       28.99        Expensive
63   Nicorette       24.99        Expensive

In [28]:
category_counts = sorted_avg_brand_price['price_category'].value_counts().reset_index()
category_counts.columns = ['price_category', 'count']

fig = px.pie(
    category_counts,
    values='count',
    names='price_category',
    title='Distribution of Brands by Price Category',
    color_discrete_sequence=px.colors.qualitative.Set3
)

fig.show()

### by Type and Price

In [29]:
apotheke_products['price_euro'] = apotheke_products['price'].str.replace(',', '.').str.extract(r'(\d+\.\d+)').astype(float)

avg_price_by_type = apotheke_products.groupby('type')['price_euro'].mean().reset_index()

avg_price_by_type['price_category'] = pd.cut(avg_price_by_type['price_euro'], bins=bins, labels=labels)

sorted_avg_type_price = avg_price_by_type.sort_values(by='price_euro', ascending=True)

sorted_avg_type_price.head()

type  price_euro price_category
28               Nasendosierspray    4.256667          Cheap
30                   Nasentropfen    4.423333          Cheap
32                       Pflaster    4.620000          Cheap
44  Tabletten, magensaftresistent    4.790000          Cheap
6                     Dosierspray    4.890000          Cheap

In [30]:
category_counts = sorted_avg_type_price['price_category'].value_counts().reset_index()
category_counts.columns = ['price_category', 'count']

fig = px.pie(
    category_counts,
    values='count',
    names='price_category',
    title='Distribution of Type by Price Category',
    color_discrete_sequence=px.colors.qualitative.Set3
)

fig.show()

## Bonus Task

In [31]:
import pandas as pd

pzn_products = pd.read_csv('20241216_export_pharmacy_receiptdata_product.csv')

pzn_products['pzn'] = pzn_products['pzn'].astype(str).str.zfill(8)

pzn_products.head()

pzn                product_name
0  16762396   HANSAPLAST SPRUEHPFLASTER
1  03643419     NICORETTE 2MG FRESHMINT
2  07263487   PARACETAMOL RATIO LOESUNG
3  09298432        EUCERIN SUN KIDS 50+
4  04778073  HANSAPLAST FIX CLA5MX2.5CM

In [32]:
def verify_pzn(pzn):
    if len(pzn) != 8 or not pzn.isdigit():
        raise ValueError("PZN must be an 8-digit numeric string.")
    
    weighted_sum = sum(int(digit) * (index + 1) for index, digit in enumerate(pzn[:-1]))
    
    check_digit = int(pzn[-1])
    expected_check_digit = weighted_sum % 11
    
    return check_digit == expected_check_digit and expected_check_digit != 10

In [33]:
pzns = ['11261117', '36434191', '36434197']
results = {pzn: verify_pzn(pzn) for pzn in pzns}

for pzn, is_valid in results.items():
    print(f"PZN {pzn}: {'Valid' if is_valid else 'Invalid'}")

PZN 11261117: Valid
PZN 36434191: Invalid
PZN 36434197: Valid


In [34]:
pzn_products['is_valid_pzn'] = pzn_products['pzn'].apply(verify_pzn)

pzn_products.to_csv('pzn_products_with_validation.csv', index=False)

pzn_products.head()

pzn                product_name  is_valid_pzn
0  16762396   HANSAPLAST SPRUEHPFLASTER          True
1  03643419     NICORETTE 2MG FRESHMINT          True
2  07263487   PARACETAMOL RATIO LOESUNG          True
3  09298432        EUCERIN SUN KIDS 50+          True
4  04778073  HANSAPLAST FIX CLA5MX2.5CM          True

In [35]:
import plotly.express as px

pzn_distribution = pzn_products['is_valid_pzn'].value_counts().reset_index()
pzn_distribution.columns = ['is_valid_pzn', 'count']
pzn_distribution['is_valid_pzn'] = pzn_distribution['is_valid_pzn'].map({True: 'Valid', False: 'Invalid'})

fig = px.pie(
    pzn_distribution,
    values='count',
    names='is_valid_pzn',
    title='Distribution of Valid and Invalid PZNs',
    color_discrete_sequence=px.colors.qualitative.Set2
)

fig.show()

## Display Manufacturers on Map

### Manufacturer Address Collection

https://www.aponeo.de/

In [17]:
import pandas as pd
import time
import random
import re
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC

def setup_driver():
    options = webdriver.ChromeOptions()
    options.add_argument("--headless")
    options.add_argument("--no-sandbox")
    options.add_argument("--disable-dev-shm-usage")
    return webdriver.Chrome(service=Service(ChromeDriverManager().install()), options=options)

def extract_address():
    try:
        all_paragraphs = driver.find_elements(By.TAG_NAME, "p")
        all_texts = [p.text.strip() for p in all_paragraphs if p.text.strip()]

        for text in all_texts:
            lines = text.split("\n")
            
            if len(lines) >= 3:
                street = lines[1].strip()
                city_info = lines[2].strip()
                
                if re.search(r"\b\d{5}\b", city_info):
                    return f"{street}, {city_info}, Germany"

        return "Not found"
    
    except Exception as e:
        print(f"Error extracting address: {e}")
        return "Not found"

def search_manufacturer_and_extract_address(manufacturer_name):
    try:
        driver.get("https://www.aponeo.de/")
        time.sleep(random.uniform(3, 5))

        try:
            consent_button = WebDriverWait(driver, 5).until(
                EC.element_to_be_clickable((By.ID, "cmpwelcomebtnyes"))
            )
            consent_button.click()
        except:
            pass

        search_box = WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "q")))
        search_box.clear()
        search_box.send_keys(manufacturer_name)
        search_box.send_keys(Keys.RETURN)
        time.sleep(random.uniform(3, 5))

        first_product = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.CSS_SELECTOR, "a.apn-product-list-product-name.stretched-link"))
        )
        driver.execute_script("arguments[0].click();", first_product)
        time.sleep(random.uniform(3, 5))

        full_address = extract_address()

        return {"manufacturer": manufacturer_name, "address": full_address}

    except Exception as e:
        print(f"Error occurred for {manufacturer_name}: {e}")
        return {"manufacturer": manufacturer_name, "address": "Not found"}

driver = setup_driver()
manufacturer_df = pd.read_csv("manufacturers_names.csv")

if "manufacturer" not in manufacturer_df.columns:
    raise ValueError("CSV file must have a column named 'manufacturer'.")

manufacturers = manufacturer_df["manufacturer"].dropna().unique()

results = []
for manufacturer in manufacturers:
    result = search_manufacturer_and_extract_address(manufacturer)
    print(f"{result['manufacturer']}: {result['address']}")
    results.append(result)

driver.quit()

results_df = pd.DataFrame(results)
results_df.to_csv("manufacturers.csv", index=False)

print("\nFinal Results Saved in manufacturers.csv")

Beiersdorf AG Eucerin: Beiersdorfstraße 1-9, 20245 Hamburg, Germany
Beiersdorf AG: Beiersdorfstraße 1-9, 20245 Hamburg, Germany
Johnson & Johnson GmbH (OTC): Johnson & Johnson Platz 2, 41470 Neuss, Germany
MCM KLOSTERFRAU Vertr. GmbH: Geronsmühlengasse 1-11, 50670 Köln, Germany
Bayer Vital GmbH: Romaneystraße 11, 51063 Köln, Germany
ratiopharm GmbH: Graf-Arco-Str. 3, 89079 Ulm, Germany
STADA Consumer Health Deutschland GmbH: Stadastr. 2-18, 61118 Bad Vilbel, Germany
Hexal AG: Industriestr. 25, 83607 Holzkirchen, Germany
Haleon Germany GmbH: Barthstr. 4, 80339 München, Germany
Bionorica SE: Kerschensteinerstr. 11-15, 92318 Neumarkt, Germany
A. Nattermann & Cie GmbH: Brüningstr. 50, 65929 Frankfurt am Main, Germany
WICK Pharma - Zweigniederlassung der Procter & Gam: Sulzbacher Str. 40-50, 65824 Schwalbach am Taunus, Germany
Reckitt Benckiser Deutschland GmbH: Darwinstraße 2-4, 69115 Heidelberg, Germany
Engelhard Arzneimittel GmbH & Co.KG: Herzbergstr. 3, 61138 Niederdorfelden, Germany
L'

### Address Analysis

In [13]:
import pandas as pd

manufacturers = pd.read_csv("manufacturers.csv")
print(f"Number of manufacturers {len(manufacturers)}")
manufacturers.head()

Number of manufacturers 40


manufacturer  \
0         Beiersdorf AG Eucerin   
1                 Beiersdorf AG   
2  Johnson & Johnson GmbH (OTC)   
3   MCM KLOSTERFRAU Vertr. GmbH   
4              Bayer Vital GmbH   

                                           address   latitude  longitude  \
0     Beiersdorfstraße 1-9, 20245 Hamburg, Germany  53.583019   9.958834   
1            Unnastraße 48, 20253 Hamburg, Germany  53.583019   9.958834   
2  Johnson & Johnson Platz 2, 41470 Neuss, Germany  51.130505   6.734413   
3      Geronsmühlengasse 1-11, 50670 Köln, Germany  50.944539   6.946518   
4            Romaneystraße 11, 51063 Köln, Germany  50.968321   7.023328   

         federal_state  
0              Unknown  
1              Unknown  
2  Nordrhein-Westfalen  
3  Nordrhein-Westfalen  
4  Nordrhein-Westfalen

In [24]:
address_counts = manufacturers['address'].value_counts()
duplicate_addresses = address_counts[address_counts > 1].index
duplicate_addresses_df = manufacturers[manufacturers['address'].isin(duplicate_addresses)]
grouped_addresses_df = duplicate_addresses_df.groupby("address")["manufacturer"].apply(list).reset_index()
print(f"Number of duplicate addresses: {len(grouped_addresses_df)}")
grouped_addresses_df

Number of duplicate addresses: 1


address  \
0  Beiersdorfstraße 1-9, 20245 Hamburg, Germany   

                             manufacturer  
0  [Beiersdorf AG Eucerin, Beiersdorf AG]

In [3]:
manufacturers = pd.read_csv("manufacturers.csv")

manufacturers.loc[manufacturers["manufacturer"] == "Beiersdorf AG", "address"] = "Unnastraße 48, 20253 Hamburg, Germany"

manufacturers.to_csv("manufacturers.csv", index=False)

### Retrieving Coordinates

In [4]:
import pandas as pd
from geopy.geocoders import Nominatim
from geopy.exc import GeocoderTimedOut

manufacturers = pd.read_csv("manufacturers.csv")

geolocator = Nominatim(user_agent="geo_locator")

def get_coordinates(address):
    try:
        location = geolocator.geocode(address, timeout=10)
        if location:
            print(f"Address: {address}, Latitude: {location.latitude}, Longitude: {location.longitude}")
            return location.latitude, location.longitude
        return None, None
    except GeocoderTimedOut:
        print(f"Timeout for address: {address}")
        return None, None

manufacturers["latitude"], manufacturers["longitude"] = zip(*manufacturers["address"].apply(lambda x: get_coordinates(x)))

manufacturers.to_csv("manufacturers.csv", index=False)

print("\nUpdated manufacturers.csv saved successfully with latitude & longitude!")

Address: Beiersdorfstraße 1-9, 20245 Hamburg, Germany, Latitude: 53.5830117, Longitude: 9.9587777
Address: Unnastraße 48, 20253 Hamburg, Germany, Latitude: 53.579424, Longitude: 9.959948442576248
Address: Johnson & Johnson Platz 2, 41470 Neuss, Germany, Latitude: 51.130505, Longitude: 6.7344133
Address: Romaneystraße 11, 51063 Köln, Germany, Latitude: 50.9683214, Longitude: 7.0233280960862
Address: Graf-Arco-Str. 3, 89079 Ulm, Germany, Latitude: 48.361343500000004, Longitude: 9.939141450000005
Address: Stadastr. 2-18, 61118 Bad Vilbel, Germany, Latitude: 50.2023586, Longitude: 8.74550326843541
Address: Industriestr. 25, 83607 Holzkirchen, Germany, Latitude: 47.8797816, Longitude: 11.712935273313718
Address: Barthstr. 4, 80339 München, Germany, Latitude: 48.1396386, Longitude: 11.5276663
Address: Kerschensteinerstr. 11-15, 92318 Neumarkt, Germany, Latitude: 49.2634687, Longitude: 11.4698866
Address: Brüningstr. 50, 65929 Frankfurt am Main, Germany, Latitude: 50.097564277538034, Longitud

In [10]:
import pandas as pd

manufacturers = pd.read_csv("manufacturers.csv")

missing_coordinates = manufacturers[manufacturers["latitude"].isna() | manufacturers["longitude"].isna()]
missing_coordinates

manufacturer                                      address  \
3  MCM KLOSTERFRAU Vertr. GmbH  Geronsmühlengasse 1-11, 50670 Köln, Germany   

   latitude  longitude        federal_state  
3       NaN        NaN  Nordrhein-Westfalen

In [1]:
import pandas as pd
from geopy.geocoders import Nominatim
from geopy.exc import GeocoderTimedOut

manufacturers = pd.read_csv("manufacturers.csv")

geolocator = Nominatim(user_agent="geo_locator")

def get_coordinates(address):
    try:
        location = geolocator.geocode(address, timeout=10)
        if location:
            print(f"Address: {address}, Latitude: {location.latitude}, Longitude: {location.longitude}")
            return location.latitude, location.longitude
        return None, None
    except GeocoderTimedOut:
        print(f"Timeout for address: {address}")
        return None, None

get_coordinates("Geronsmühlengasse 1-11, 50670 Köln, Germany")

(None, None)

In [12]:
manufacturers = pd.read_csv("manufacturers.csv")

manufacturers.loc[manufacturers["address"] == "Geronsmühlengasse 1-11, 50670 Köln, Germany", "latitude"] = 50.9445388
manufacturers.loc[manufacturers["address"] == "Geronsmühlengasse 1-11, 50670 Köln, Germany", "longitude"] = 6.9465184

manufacturers.to_csv("manufacturers.csv", index=False)

### Displaying on Map

In [14]:
import pandas as pd
import folium

manufacturers = pd.read_csv("manufacturers.csv")

germany_map = folium.Map(location=[51.1657, 10.4515], zoom_start=6)

for index, row in manufacturers.iterrows():
    if not pd.isna(row["latitude"]) and not pd.isna(row["longitude"]):
        folium.Marker(
            location=[row["latitude"], row["longitude"]],
            popup=row["manufacturer"],
            tooltip=row["manufacturer"]
        ).add_to(germany_map)

germany_map

### Retriving Federal States

In [11]:
import pandas as pd
from geopy.geocoders import Nominatim
from geopy.exc import GeocoderTimedOut

manufacturers = pd.read_csv("manufacturers.csv")

geolocator = Nominatim(user_agent="geo_locator")

def get_state(latitude, longitude):
    try:
        location = geolocator.reverse((latitude, longitude), exactly_one=True, timeout=10)
        if location:
            address = location.raw.get('address', {})
            state = address.get('state', 'Unknown')
            print(f"Latitude: {location.latitude}, Longitude: {location.longitude}: {state}")
            return state
        return "Unknown"
    except GeocoderTimedOut:
        print(f"Timeout for coordinates: {latitude}, {longitude}")
        return "Unknown"

manufacturers["federal_state"] = manufacturers.apply(lambda row: get_state(row["latitude"], row["longitude"]) if pd.notnull(row["latitude"]) else "Unknown", axis=1)

manufacturers.to_csv("manufacturers.csv", index=False)

Latitude: 53.5828785, Longitude: 9.9587698: Unknown
Latitude: 53.5828785, Longitude: 9.9587698: Unknown
Latitude: 51.130505, Longitude: 6.7344133: Nordrhein-Westfalen
Latitude: 50.944915699999996, Longitude: 6.946709833834276: Nordrhein-Westfalen
Latitude: 50.9683214, Longitude: 7.0233280960862: Nordrhein-Westfalen
Latitude: 48.361343500000004, Longitude: 9.939141450000005: Baden-Württemberg
Latitude: 50.2023586, Longitude: 8.74550326843541: Hessen
Latitude: 47.8797816, Longitude: 11.712935273313718: Bayern
Latitude: 48.1396386, Longitude: 11.5276663: Bayern
Latitude: 49.263102599999996, Longitude: 11.469307880605935: Bayern
Latitude: 50.097043049999996, Longitude: 8.541320582207575: Hessen
Latitude: 50.1439039, Longitude: 8.533459952209451: Hessen
Latitude: 49.4007328, Longitude: 8.6715541: Baden-Württemberg
Latitude: 50.1924521, Longitude: 8.7931221: Hessen
Latitude: 51.25262305, Longitude: 6.773576386805891: Nordrhein-Westfalen
Latitude: 52.5078939, Longitude: 13.374902485469432: Un

### Categorization Manufacturers by Federal States

In [16]:
import pandas as pd

manufacturers = pd.read_csv("manufacturers.csv")

grouped_by_state = manufacturers.groupby("federal_state").agg(
    manufacturers=("manufacturer", lambda x: ', '.join(x)),
    manufacturer_count=("manufacturer", "count")
).reset_index()

grouped_by_state = grouped_by_state.sort_values(by='manufacturer_count', ascending=False)
grouped_by_state

federal_state                                      manufacturers  \
1               Bayern  Hexal AG, Haleon Germany GmbH, Bionorica SE, O...   
3  Nordrhein-Westfalen  Johnson & Johnson GmbH (OTC), MCM KLOSTERFRAU ...   
6              Unknown  Beiersdorf AG Eucerin, Beiersdorf AG, Zentiva ...   
0    Baden-Württemberg  ratiopharm GmbH, Reckitt Benckiser Deutschland...   
2               Hessen  STADA Consumer Health Deutschland GmbH, A. Nat...   
5   Schleswig-Holstein  G. Pohl-Boskamp GmbH & Co. KG, GALENpharma Gmb...   
4             Saarland                        URSAPHARM Arzneimittel GmbH   

   manufacturer_count  
1                  11  
3                   8  
6                   7  
0                   6  
2                   4  
5                   3  
4                   1

### Unknown Federal States?

In [9]:
get_state(53.58301884113736,9.958833522518514)

Latitude: 53.5828785, Longitude: 9.9587698: Unknown


'Unknown'

In [14]:
unknonw_federal_state_manufacturers = manufacturers[manufacturers['federal_state'] == 'Unknown']
unknonw_federal_state_manufacturers

manufacturer  \
0                      Beiersdorf AG Eucerin   
1                              Beiersdorf AG   
15                       Zentiva Pharma GmbH   
20  Dr. Gerhard Mann Chem.-pharm.Fabrik GmbH   
29                        Aristo Pharma GmbH   
32                          Thea Pharma GmbH   
35      DR. KADE Pharmazeutische Fabrik GmbH   

                                              address   latitude  longitude  \
0        Beiersdorfstraße 1-9, 20245 Hamburg, Germany  53.583019   9.958834   
1               Unnastraße 48, 20253 Hamburg, Germany  53.583019   9.958834   
15                Linkstraße 2, 10785 Berlin, Germany  52.507894  13.374902   
20  Brunsbütteler Damm 165-173, 13581 Berlin, Germany  52.533169  13.158416   
29       Wallenroder Str. 8-10, 13435 Berlin, Germany  52.603641  13.341277   
32              Schillerstr. 3, 10625 Berlin, Germany  52.511235  13.321067   
35                  Rigistr. 2, 12277 Berlin, Germany  52.411964  13.378748   

   federal_state  
0        Unknown  
1        Unknown  
15       Unknown  
20       Unknown  
29       Unknown  
32       Unknown  
35       Unknown

### Display Federal States on Map

In [15]:
import pandas as pd
import folium
import geopandas as gpd
import random

df = pd.read_csv("manufacturers.csv")

geojson_file = "1_sehr_hoch.geo.json"
geojson_data = gpd.read_file(geojson_file)

print("GeoJSON Columns:", geojson_data.columns)

state_column = None
for col in geojson_data.columns:
    if "name" in col.lower():
        state_column = col
        break

if not state_column:
    raise ValueError("No valid column found for federal state names in GeoJSON!")

print(f"Using '{state_column}' as the federal state column.")

federal_states_map = folium.Map(location=[51.1657, 10.4515], zoom_start=6)

state_colors = {feature: f"#{random.randint(0, 0xFFFFFF):06x}" for feature in geojson_data[state_column]}

folium.GeoJson(
    geojson_data,
    name="Bundesländer",
    style_function=lambda feature: {
        "fillColor": state_colors.get(feature["properties"][state_column], "gray"),
        "color": "black",
        "weight": 1,
        "fillOpacity": 0.5
    }
).add_to(federal_states_map)

for index, row in df.iterrows():
    if not pd.isna(row["latitude"]) and not pd.isna(row["longitude"]):
        folium.Marker(
            location=[row["latitude"], row["longitude"]],
            popup=f"{row['manufacturer']} ({row['federal_state']})",
            tooltip=row["manufacturer"],
            icon=folium.Icon(color="blue", icon="info-sign")
        ).add_to(federal_states_map)

federal_states_map

GeoJSON Columns: Index(['id', 'name', 'type', 'geometry'], dtype='object')
Using 'name' as the federal state column.
